## ELEX 4653 Quiz 2

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

### Question 1

Write a function `safe(f,l)` that calls the function `f()` with successive values from the list `l` and returns
an integer which is a count of the number of times calling the function `f()` raised a `ValueError`.
Other exceptions should be ignored.

For example, if `f(x)` is defined as:

```
def f(x):
    if x < 0:
        raise(ValueError)
    return 2/x
```

then `safe(f, [-1, 2, 2, 1, 0, 1, 1, -1])` should return `2`.

### Question 2

Write a function `process(f,l)` that returns a list of values
returned by the function `f` when called with successive values from the list `l`.  Your function _must_ use the built-in `map` iterator.

For example, if `f(x)` is defined as:
```
def f(x):
    return 2*x
```
Then `process(f,[1,2,3])` should return `[2,4,6]`.

### Question 3

Write a function `environ()` that returns
the float value returned by the function `math.cos()` of the value `math.e`.  For example, `math.cos(math.pi)` would return `-1.0`.

In [4]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    import traceback
    
    n = 0     # question number
    trial = 0 # test number
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.search(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.search(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l

    # list of n random integers
    def randints(n,*args,**kwargs):
        return [randint(*args,**kwargs) for _ in range(n)]

    # list of uniformly distribute random numbers
    def randoms(n,*args,**kwargs):
        return [random.uniform(*args,**kwargs) for _ in range(n)]
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    
    import math
    def roundn(num, n):
        return 0 if not num else round(num, -int(math.floor(math.log10(abs(num)))) + (n - 1))

    def ch(s,n=(1,1)):
        return randwords(1,chars=s,nl=n)[0]

    import ast, inspect
    def uses(f,s):
        for t in ast.walk(ast.parse(inspect.getsource(f))):
            if isinstance(t, ast.Call):
                if isinstance(t.func, ast.Name) and t.func.id == s:
                    return True
        return False

    def Q(f,*a,rounding=False):
        oa = copy.deepcopy(a)
        r = f(*a)
        r = roundn(r,2) if rounding else r
        return (r,f"{f.__name__}{repr(oa)} returns {repr(r)}")

 
    def Q1():
        def f(x):
            r = randint(0,1)
            if r:
                raise(ValueError)
            elif randint(0,1):
                raise(Exception)
            else:
                return x
        return Q(safe,f,[randint(0,9) for i in range(randint(5,8))])


    def Q2():
        def f(x):
            return randint(0,9)
        if not uses(process,'map'):
            return ([],"process() does not use the map() iterator.")
        return Q(process,f,randwords(randint(5,8)))

    def Q3():
        return Q(environ)
  
    hashvalues = '''
LgOnZEo+6x5+LgOn6x5+6x5+gBsn6x5+Vj+XLgOn
BZSDDQQTMZP60Nag45IXGiwfzFj8RZjzZX/90ftZ
EFhDEFhDEFhDEFhDEFhDEFhDEFhDEFhDEFhDEFhD
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        trial = 0
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                traceback.print_exc()
                err = f"Error during test {n}: {e}"
            trial += 1
        if testing:
           newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)


labcheck(0)